<a href="https://colab.research.google.com/github/Manvi1718/Emotion_Analysis/blob/main/Emotion_analysis.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import os
os.environ["KAGGLE_USERNAME"] = "annmittal"
os.environ["KAGGLE_KEY"] ="b36a820c483a21bd0633e9b284bbc42c"

!kaggle datasets download -d shawon10/ckplus

  0% 0.00/3.63M [00:00<?, ?B/s]
100% 3.63M/3.63M [00:00<00:00, 196MB/s]


In [2]:
!unzip ckplus.zip

Archive:  ckplus.zip
  inflating: CK+48/anger/S010_004_00000017.png  
  inflating: CK+48/anger/S010_004_00000018.png  
  inflating: CK+48/anger/S010_004_00000019.png  
  inflating: CK+48/anger/S011_004_00000019.png  
  inflating: CK+48/anger/S011_004_00000020.png  
  inflating: CK+48/anger/S011_004_00000021.png  
  inflating: CK+48/anger/S014_003_00000028.png  
  inflating: CK+48/anger/S014_003_00000029.png  
  inflating: CK+48/anger/S014_003_00000030.png  
  inflating: CK+48/anger/S022_005_00000030.png  
  inflating: CK+48/anger/S022_005_00000031.png  
  inflating: CK+48/anger/S022_005_00000032.png  
  inflating: CK+48/anger/S026_003_00000013.png  
  inflating: CK+48/anger/S026_003_00000014.png  
  inflating: CK+48/anger/S026_003_00000015.png  
  inflating: CK+48/anger/S028_001_00000022.png  
  inflating: CK+48/anger/S028_001_00000023.png  
  inflating: CK+48/anger/S028_001_00000024.png  
  inflating: CK+48/anger/S029_001_00000017.png  
  inflating: CK+48/anger/S029_001_00000018.png  

In [3]:
import torch
from torch import nn
import torchvision
from torch.utils import data
import torchvision.datasets as datasets
import torchvision.transforms as transforms
import albumentations
from albumentations import pytorch as AT

In [4]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import csv
from PIL import Image

In [5]:
use_cuda= torch.cuda.is_available()
device = torch.device("cuda" if use_cuda else "cpu")

In [6]:
device

device(type='cuda')

In [7]:
!pip install split-folders

In [8]:
import splitfolders

In [9]:
#Splitting dataset into train ,test and validation

original="/content/drive/MyDrive/pytorch/ck+/CK+48"
splitted="/content/drive/MyDrive/pytorch/ck+/CK+48 splitted"

splitfolders.ratio(original,output=splitted,seed=1337,ratio=(.75,.25),group_prefix=None)

Copying files: 178 files [00:38,  3.18 files/s]

KeyboardInterrupt: ignored

In [12]:
#Converting image dataset in folder to readable csv file

#Train folder to csv
image_folder = "/content/drive/MyDrive/pytorch/ck+/CK+48 splitted/train_d"
image_files = [f for f in os.listdir(image_folder) if f.endswith(".jpg") or f.endswith(".png")]

data = []
for image_file in image_files:
    image_path = os.path.join(image_folder, image_file)
    emotion_label = image_file.split("_")[0]

    image = Image.open(image_path)
    image = image.convert("L")
    pixel_values = list(image.getdata())

    data.append((emotion_label, pixel_values))

csv_file = "train.csv"
with open(csv_file, mode="w", newline="") as file:
    writer = csv.writer(file)
    writer.writerow(["Emotion", "Pixels"])

    for emotion_label, pixel_values in data:
        writer.writerow([emotion_label, *pixel_values])

#Test folder to csv
image_folder = "/content/drive/MyDrive/pytorch/ck+/CK+48 splitted/test_d"
image_files = [f for f in os.listdir(image_folder) if f.endswith(".jpg") or f.endswith(".png")]

data = []
for image_file in image_files:
    image_path = os.path.join(image_folder, image_file)
    emotion_label = image_file.split("_")[0]

    image = Image.open(image_path)
    image = image.convert("L")
    pixel_values = list(image.getdata())

    data.append((emotion_label, pixel_values))

csv_file = "test.csv"
with open(csv_file, mode="w", newline="") as file:
    writer = csv.writer(file)
    writer.writerow(["Emotion", "Pixels"])

    for emotion_label, pixel_values in data:
        writer.writerow([emotion_label, *pixel_values])


In [11]:
train_df = pd.read_csv("train.csv")
train_df.head(100)

Emotion  \
contempt 220 219 220 219 202 153 64  49  42  38  36  32  37  52  74  99  120 132 142 147 147 145 149 150 154 154 151 150 143 141 139 136 131 123 104 86  69  54  42  36  35  33  33  34  37  73  159 180 219 219 217 207 172 89 44  40  37  36  35  44  64  91  115 128 142 149 151 151 152 155 155 160 165 166 164 158 145 139 143 141 140 133 126 112 93  75  57  43  36  34  33  33  37  36  92  178 219 216 215 188 124 49 40  37  34  36  47  70  97  120 129 141 151 153 156 158 160 161 164 168 175 177 174 172 156 148 149 148 143 138 133 124 114 100 82  61  45  36  34  32  33  37  42  136 217 219 204 158 70 39 36  34  37  48  69  98  119 129 135 146 155 163 164 164 166 166 169 172 175 177 177 172 166 162 159 152 144 139 135 127 121 114 102 82  60  47  37  32  32  34  38  68  218 212 169 105 37 36 35 37  49  71  92  113 125 130 139 151 159 169 170 169 169 169 171 170 171 175 174 170 167 163 160 153 145 137 132 127 120 117 110 98  82  67  49  36  32  35  38  44  218 183 136 54 36 34 35 44  72  96  114 125 131 133 146 153 162 169 169 169 170 170 171 170 171 172 171 167 162 159 157 153 146 139 134 128 122 119 117 112 102 90  71  50  36  31  36  41  213 164 99 41 34 34 42 67  97  116 127 133 135 138 149 154 161 166 167 168 169 170 169 168 169 171 170 167 164 162 157 152 146 140 135 128 125 123 123 117 114 105 89  70  47 35  32  36  188 142 65 35 32 37 51  81  113 129 135 140 139 138 150 155 160 165 167 167 169 168 169 171 170 171 169 168 167 166 160 154 148 141 135 130 127 126 127 124 117 112 99  81 57 36 32  34  182 122 46 31 34 40 61  95  123 137 143 143 143 148 151 156 161 167 170 170 171 171 170 171 172 173 171 171 170 168 164 156 150 145 138 133 129 129 128 127 121 113 101 81 64 40 30  31  175 102 41 31 33 41 71  100 130 142 147 147 149 152 154 157 163 167 171 172 172 172 172 174 176 176 174 173 173 173 168 158 150 146 139 134 130 130 129 126 123 115 100 80 62 44 32 27  168 95 41 32 33 47 74  105 136 144 148 149 153 156 159 161 165 169 173 173 172 171 170 171 173 171 171 172 171 171 168 159 152 149 143 139 135 133 131 127 122 119 108 86 58 44 32 29 165 93 38 33 33 49 81  116 141 146 147 153 159 161 162 165 168 171 172 168 167 165 165 167 166 164 161 162 161 160 162 157 155 153 149 144 140 139 134 129 123 121 114 98 71 43 32 30 172 91 41 34 33 51 91  130 145 146 142 142 145 149 147 151 156 156 149 148 151 150 154 159 160 158 153 147 142 142 141 134 125 122 123 121 117 117 115 123 124 122 118 111 88 57  33 30  187 97  47 34 39 64 112 138 145 129 104 92  89  85  79  80  83  89  94  106 122 130 143 149 153 148 141 129 127 121 107 84  74  74  70  71  74  78  80  86  101 116 122 120 108 72 38  29  197 117 50 34 37 84  135 144 130 105 94  97  105 107 104 97  89  89  93  101 109 118 135 143 149 141 133 120 115 110 101 91  87  88  93  91  90  90  89  86  88  103 119 123 117 92 47  26  191 142 49 29 40  111 148 147 135 121 121 135 150 157 154 149 136 128 122 120 119 123 134 143 146 138 130 122 116 115 113 113 125 138 146 146 136 122 108 103 99  110 121 122 121 110 59 28  201 113 37 26 54  137 152 153 146 140 146 151 156 161 162 158 152 147 140 132 132 135 144 148 147 137 130 127 126 124 129 141 146 150 150 147 138 127 120 117 109 110 122 125 124 119 75  29  205 156 50 29 80  154 154 153 147 146 143 143 149 156 157 155 150 141 137 131 131 142 152 155 152 145 137 130 126 128 136 141 145 142 139 132 120 115 114 116 116 116 120 126 125 121 87  34  199 139 48 38 116 160 155 151 146 139 135 126 105 88  75  68  70  96  120 121 124 142 156 163 161 156 142 130 122 124 130 130 92  80  70  70  72  81  90  102 110 113 120 125 128 124 92  38  195 90 39 55 139 160 157 155 147 127 93  61  76  109 66  30 21  35  72  117 126 150 160 168 169 164 147 132 124 125 126 67  76  40  21  25  63  59  49  64  91  113 124 127 131 130 98  41  176 64 45 68 147 157 160 162 154 124 105 110 116 132 109 47  54  94  85  115 143 157 162 171 174 169 148 135 133 140 115 89  126 72  47  65  100 93  87  80  84  116 130 133 135 131 107 47  152 58 46 84  150 156 159 163 164 158 1

In [14]:
test_df = pd.read_csv("test.csv")
test_df.head(50)

Emotion  \
sadness  47  27  5   1   7   10  4   1   5   7   9   11  12  10  12  14  19  32  65  99  130 146 178 199 204 204 207 213 219 214 213 171 104 53  34  17  10  7   6   11  16  19  14  14  15  37  57  73  27  6   1   2   5   4   2   4   9   9   15  17  12  11  15  21  53  98  135 158 175 189 214 220 223 227 229 231 232 229 226 209 177 129 72  27  11  9   7   5   8   13  14  13  12  14  49  71  9   2   1   1   3   3   3   10  14  14  16  14  15  17  21  75  140 172 193 202 210 219 233 235 235 236 236 237 239 238 235 216 191 179 126 45  12  9   6   5   4   8   10  11  14  10  38  68  3   1   0   0   3   4   8   15  14  12  12  15  19  14  58  160 190 203 210 214 208 222 235 235 235 235 235 235 236 237 232 223 211 198 167 83  31  14  9   7   9   8   8   6   7   11  23  59  0   0   0   0   0   4   7   10  10  7   5   11  16  30  127 186 198 211 220 223 218 227 233 235 235 235 235 238 237 231 226 224 219 208 191 129 101 52  16  11  8   8   7   5   1   4   20  54  0   0   0   0   0   4   7   6   9   6   6   15  31  99  168 190 203 206 211 210 207 208 212 214 216 217 219 228 233 234 231 225 219 215 202 154 139 112 34  15  10  7   4   8   5   0   15  48  1   0   0   0   0   2   2   4   6   2   14  46  88  146 179 190 204 217 224 226 227 230 233 237 239 235 231 229 221 222 217 213 215 213 207 189 153 153 68  29  14  7   2   7   9   5   12  39  1   2   1   0   0   1   0   7   4   1   36  97  143 172 190 196 201 212 220 223 217 212 213 224 233 231 228 230 237 236 228 224 222 216 212 208 191 165 110 36  21  8   1   3   10  17  14  28  0   1   0   0   0   0   0   6   2   9   80  142 174 183 189 198 201 214 225 231 234 234 233 234 226 215 218 232 237 237 230 224 214 213 216 213 212 199 170 94  37  27  23  27  28  24  16  14  0   0   0   0   0   0   0   4   0   52  134 160 183 191 196 205 194 213 229 236 232 222 213 207 210 220 235 242 240 223 212 212 212 218 216 214 214 209 193 164 74  27  19  18  13  5   12  11  0   0   0   0   0   0   0   0   20  106 153 166 177 188 197 218 216 212 225 233 236 224 208 209 216 224 236 242 236 227 239 243 242 240 231 224 217 207 194 188 131 40  15  7   3   0   7   10  0   0   0   0   0   0   2   3   55  126 156 169 183 200 214 223 223 218 209 215 232 225 216 225 232 230 234 225 213 225 231 218 208 207 205 218 214 202 192 187 166 72  22  10  2   0   1   6   0   0   1   1   0   3   16  10  76  136 162 169 165 167 165 161 162 166 178 197 220 223 227 232 235 229 220 203 177 137 136 124 107 104 110 148 202 203 189 183 184 112 28  16  3   1   1   3   0   0   1   1   0   8   15  20  104 147 161 127 104 94  86  89  83  96  131 186 199 205 219 227 228 218 207 192 127 87  96  112 130 147 150 135 152 190 188 180 184 142 36  16  5   2   1   0   0   0   1   0   0   4   7   57  127 139 122 117 125 136 142 143 132 127 109 140 161 181 199 211 211 199 182 152 130 132 135 145 167 184 195 189 159 153 173 176 179 159 51  11  3   2   1   0   0   0   0   0   0   1   30  93  122 118 134 161 173 178 170 149 129 118 113 116 136 167 190 203 199 179 152 128 122 111 99  104 113 135 163 186 185 166 172 178 180 169 63  11  3   2   1   0   0   0   1   0   0   9   64  107 122 137 153 167 169 149 118 94  80  86  108 115 130 169 195 210 207 185 143 124 112 83  89  114 136 135 125 145 162 167 171 176 180 175 76  9   5   5   4   6   0   0   0   1   1   23  85  116 125 133 141 146 119 98  91  87  71  67  81  110 123 179 208 229 224 192 129 119 91  80  85  77  92  110 132 118 129 143 156 170 180 175 80  7   3   2   4   3   0   0   1   2   3   33  96  121 119 121 122 82  51  25  27  35  52  67  73  103 130 180 219 239 232 194 140 122 85  94  75  31  29  24  60  83  106 125 143 166 180 176 79  7   4   2   2   3   0   0   1   0   2   43  108 128 127 121 84  56  101 55  39  32  108 140 76  124 153 177 219 241 241 205 183 173 89  150 124 52  40  66  133 68  93  135 155 172 182 182 81  8   1   0   0   4   1   1   1   0   1   52  121 142 149 132 93  98  137 112 83  106 172 161 142 168 179 188 219 240 239 215 213 213 180 176 167 134 112 144 156 